In [11]:
import pandas as pd
import subprocess
import numpy as np
from subprocess import Popen, PIPE
from datetime import datetime
from pytz import UTC
import os
from time import sleep
from pytube import YouTube
import json
import pickle
import re
import traceback

In [12]:
avspeech = pd.read_csv("avspeech_train.csv", names=[
    'id', 'start', 'end', 'x', 'y'])

In [13]:
RES_TABLE = {
    '1080p': [1920, 1080],
}

In [14]:
regex="[\u2E80-\u9FFF]"#中日韓
#regex="[\u4E00-\u9FFF]"#中文

In [21]:
JOB_PATH = 'jobs.pkl'
LAST_JOB_PATH = 'job_last.txt'
AUTHOR_NAME_PATH='author_name.txt'
CHINESE_JOB_PATH='chinese_title_new2.csv'
last_job_id = None
if os.path.exists(LAST_JOB_PATH):
    last_job_id = open(LAST_JOB_PATH, 'r').read().strip()

if os.path.exists(JOB_PATH):
    jobs = pickle.load(open(JOB_PATH, 'rb'))
else:
    jobs = {}
    for i, row in avspeech.iterrows():
        _id = row['id']
        if _id not in jobs:
            jobs[_id] = []
        job = dict(row)
        job.pop('id')
        jobs[_id].append(job)
    pickle.dump(jobs, open(JOB_PATH, 'wb'))

In [22]:
def findPart(text):
    chinese=re.findall(regex,text)
    return len(text),len(chinese)


In [23]:
def download_job(_id, jobs, dirpath):
    is_downloaded = True
    for i, job in enumerate(jobs):
        output_fname = '{}-{}.mp4'.format(_id, i)
        output_path = os.path.join(dirpath, output_fname)
        if not os.path.exists(output_path):
            is_downloaded = False
    if is_downloaded:
        print('bypass exists: ', _id)
        return
    youtube_url = "https://www.youtube.com/watch?v={}".format(_id)
    sleep(12)
    yt = YouTube(youtube_url)
#     print(yt.watch_url)
    videos = sorted(filter(lambda s: s.type == 'video', yt.fmt_streams), key=lambda row: int(row.resolution.replace('p', '')), reverse=True)
    if len(videos) == 0:
        print("video not found")
        return 
    video_info = videos[0]
    tmp_path = 'tempvideo'
    xy_res = RES_TABLE.get(video_info.resolution)
    if xy_res is None:
        #print("high resolution not found")
        return
    title_text=yt.title
    if(findPart(title_text)[1]<1):
        #print('no chinese')
        return
    print(youtube_url)
    with open(AUTHOR_NAME_PATH,'a+') as fw:
        with open(AUTHOR_NAME_PATH,'r+') as fr:
            lines=fr.readlines()
            if lines.count(yt.author+"\n")>4:
                return
        fw.write(yt.author+"\n")
        
    print("download {} to {}".format(_id, tmp_path))
#     sleep(10)
    for i, job in enumerate(jobs):
        with open(CHINESE_JOB_PATH,'a+')as f:
            f.write("{},{},{},{},{}\n".format(_id,job['start'],job['end'],job['x'],job['y']))

In [24]:
start = False
for i, (_id, jobs_in_id) in enumerate(jobs.items()):
    if last_job_id is None or _id.startswith(last_job_id):
        start = True
    if not start:
        print('[bypass] {}'.format(_id))
        continue
    try:
        download_job(_id, jobs_in_id, 'avspeech/videos')
    except Exception as err:
        print(_id,err)
        if str(err) in "HTTP Error 429: Too Many Requests":
          break
    if i % 10 == 0:
        with open(LAST_JOB_PATH, 'w') as f:
            f.write(_id)

[bypass] CJoOwXcjhds
[bypass] AvWWVOgaMlk
[bypass] Y8HMIm8mdns
[bypass] akwvpAiLFk0
[bypass] Swss72CHSWg
[bypass] ymD5uLlLc0g
[bypass] DuWE-CQDlEk
[bypass] uCGKDCWxqxo
[bypass] -A9gdf3j2xo
[bypass] labiHToR5nk
[bypass] xbgfxIc-nbs
[bypass] QoQF8N5ZsQA
[bypass] 307DK9nGQhw
[bypass] 5qy9Ujv9XdM
[bypass] UBL2Vowiulk
[bypass] LcyrfLT2tto
[bypass] sujFCXbYkMo
[bypass] R0u9E8GsUXk
[bypass] bNxD_breZy8
[bypass] AQDWwktBhaw
[bypass] Dtn8xZ3BiGY
[bypass] Cy9SUMj5wGY
[bypass] 8nQBG5hvjpk
[bypass] rCp8Jae81KU
[bypass] PmD-LzPS2rg
[bypass] BrCcDt6GNkk
[bypass] IrXrbrZWflA
[bypass] 512K2S3De-A
[bypass] 01qWxISqaHg
[bypass] 2f32XSMYlDk
[bypass] lcClO5lHEjA
[bypass] q1doqKlHRuY
[bypass] tdTXVU5wN8I
[bypass] h-fSfAFufCo
[bypass] srwckJKdeS0
[bypass] DIWf1t-HzwI
[bypass] YXcVkIEMGds
[bypass] BsUzOhJ9WGU
[bypass] JjduaMIoKvI
[bypass] IlnHVjvBDU0
[bypass] zFH0QbS-l-w
[bypass] h5wT_c4fQ1o
[bypass] 3AsPqH3QaQM
[bypass] aaEA__Js2u0
[bypass] 7rYeSDHS0U0
[bypass] qpEzCs23PWE
[bypass] 8E2UlNrLNmk
[bypass] Bjvt

[bypass] Wv9vcD9QwPQ
[bypass] -jbHHlII8PU
[bypass] T9-JWQyUq94
[bypass] R9kiC22a6x8
[bypass] sARIE9qY3k8
[bypass] KF6Yyy6AW8k
[bypass] khF6Cqlud0s
[bypass] najv0J8HXhs
[bypass] FRmaxdd9dIA
[bypass] J9ORuWqvX_g
[bypass] JvjHE2kAc1I
[bypass] yj38GtYdmO0
[bypass] lXet-uaBx2o
[bypass] Wwo3Ifs0DLs
[bypass] _thdh4Lv2MI
[bypass] Yr6t9VaANGI
[bypass] b03H83nMgGo
[bypass] tQ37tbbP3zo
[bypass] ZWBGXXSJLHo
[bypass] UG9eSIeP_nw
[bypass] x7Rik_3JQ1I
[bypass] tJUjJNavOoA
[bypass] B2qzUTV1z1U
[bypass] PG_q2WiiJcw
[bypass] H9TMK4Gg8og
[bypass] OO42ZUA9bYc
[bypass] VY3T4ZC91iY
[bypass] yrm2GdNT134
[bypass] IvukAijXgLE
[bypass] A3HYUFh4ymo
[bypass] yKkkXIzkbWw
[bypass] 4PCMiQwUBxk
[bypass] WrUD68RaWiQ
[bypass] bl-Uk9lvIJw
[bypass] X5gWl1yVEyI
[bypass] VLPywiYO0wg
[bypass] ddK1ui1UUys
[bypass] 7p84YJpKGpM
[bypass] I0UPWVv66gU
[bypass] 6IBB59GLpTo
[bypass] F5A59NXfbnA
[bypass] rnJfBqPoCbw
[bypass] t0sYwpVd2Vg
[bypass] khFT6YNDEJg
[bypass] ReDXII-f3ao
[bypass] TCwgrh4SW6Q
[bypass] gE-IHo9hpKw
[bypass] TzZs

[bypass] IA9v82qOfR8
[bypass] 9lkyjt0j3Bs
[bypass] HKGDTTXq5do
[bypass] 212i9RgRyLQ
[bypass] pP75G0-CeqI
[bypass] z3CWh5-qmbc
[bypass] URiNfztVdHU
[bypass] v3ovpjYXjXg
[bypass] nglx5Wqh_jw
[bypass] _Xtjyl8SEvU
[bypass] oa6YquRwV0s
[bypass] rMXBuGnSdJY
[bypass] 6TW22OUA_MM
[bypass] ScGMG3O0Opk
[bypass] Xc-zTs7zUgg
[bypass] 2gLxxvg5h5Y
[bypass] 4sOkkxsooQk
[bypass] 7A56D95GXRE
[bypass] IcVhPBfhTxs
[bypass] FthFVvE3czg
[bypass] cWfbH0zYnYw
[bypass] bWVd1I6_4HQ
[bypass] DQAmXBEZgK8
[bypass] iVCoKxwCi70
[bypass] a-js7NXgDVA
[bypass] 5M1uI8DD8qg
[bypass] vRH6kvpL8rs
[bypass] 8ZtcR_pCrgg
[bypass] Ix0Lj7ChbRk
[bypass] BJ-XxYqZ6-0
[bypass] PKtSAirA_T8
[bypass] 5tuuf1ZPyZ0
[bypass] HrPlNOw7wGk
[bypass] wTzzPIB2zeo
[bypass] nv_A1nSUAi8
[bypass] yk5KkKDHzCg
[bypass] gNtE41J97m4
[bypass] lPzn6H0VwJU
[bypass] nx4sRl0AxPM
[bypass] AXgTXrTgvRU
[bypass] xco03iE8bxU
[bypass] UzqRtNF-Do8
[bypass] dwSMhkRf4zA
[bypass] kGaL_KJhWNA
[bypass] 4O-eomW0hzw
[bypass] l85J1MLvi-Y
[bypass] _hE7MOu2trs
[bypass] Avjn

[bypass] EzwS8jm8QVc
[bypass] BNdjt45UmV0
[bypass] dygjkDWPF-k
[bypass] IEQfJoAWRxA
[bypass] gq1BhxUluas
[bypass] V70EPZ-h3ho
[bypass] J5Mb2jiirUM
[bypass] oeRq1yEk7-I
[bypass] x9RAqEQ6624
[bypass] jexnhNfOzHg
[bypass] 1C0Pz4cD80Q
[bypass] W7XQFpApMrA
[bypass] 4xFNAb0w_QM
[bypass] 6BXdCpd4R2E
[bypass] MR2t5J1342s
[bypass] O4kf3-Msgf4
[bypass] IsumrIkHOIY
[bypass] eaq_nhX2xKA
[bypass] 6tAu4tEw0po
[bypass] tpCIbYLPAqQ
[bypass] CCzJHV1HqmI
[bypass] sESsLiHWkDM
[bypass] uD9hObdnDk0
[bypass] xI4gGIlsssY
[bypass] dSeHnhFhPjg
[bypass] Yzaszyvkelc
[bypass] 3aBDBDnTNzo
[bypass] zOGSMg-8eFk
[bypass] z2JPWS_XbeU
[bypass] oPW6VuPuC0M
[bypass] APU3iBoxIUo
[bypass] GZsvYnwxDpI
[bypass] o8sRRJXkC3s
[bypass] o6Bnv4gRIpg
[bypass] sVtFatHOXdU
[bypass] oZs3a51zTAE
[bypass] XoeJagggJB4
[bypass] ORw9C8ci0QY
[bypass] lXgCQ1db-KE
[bypass] TFMSVIcA_yU
[bypass] SrII-3tRqxY
[bypass] 2EaLVHSBL04
[bypass] vlwBVrPGc7A
[bypass] hy96rU8Jn1s
[bypass] ijm6r2h5128
[bypass] Ixiuk4571pk
[bypass] eN5YE7Ss1aQ
[bypass] KWy2

[bypass] AV4dqnkxGQM
[bypass] tjiXmRl_Bqs
[bypass] uEcNtmcMq7g
[bypass] 36yK92Q6xN0
[bypass] R3n6t2PLAcQ
[bypass] vPxJMqt5Yko
[bypass] eRvA9qDBUXU
[bypass] mthLL7h2fMg
[bypass] nbyopTabrXE
[bypass] 3F_Q-5OhWUs
[bypass] KYiO2oLU9C8
[bypass] qz7ulPouWfo
[bypass] umCV7sA7vWw
[bypass] DK64MV-KYtI
[bypass] ieR2TXe-5_o
[bypass] kTN6TFhXiIE
[bypass] iSJhsbxfGYc
[bypass] 090aMgW3l6w
[bypass] ATby2TPngZo
[bypass] 1dxUOAXlVKw
[bypass] Jq7ScXPWl7k
[bypass] ZbT0SdvYKpw
[bypass] cDU7sZgvxyA
[bypass] Snuzf61kkbU
[bypass] 4HBJa279i8M
[bypass] 7gAUz59e66A
[bypass] mNN5PHHGl6s
[bypass] Iu6h9IsDVw8
[bypass] 89A5g2UGnDs
[bypass] RI-RT27v3V0
[bypass] hVRg5cHeXZ4
[bypass] o_EzVm7nxrs
[bypass] Y8VIaKfcnaE
[bypass] GK68Tc6Q5Vc
[bypass] 4VYjLM3WHnY
[bypass] enIozm2EgRk
[bypass] 1a6Izn3xN_s
[bypass] IMpgfdXTTeY
[bypass] krHmZT1b1zQ
[bypass] UmKWlF9MZjs
[bypass] dydx3julMvA
[bypass] b2VDKHdOT_U
[bypass] HivmYdhmv7Y
[bypass] HgtlyAtJDfQ
[bypass] VX35xfmiMCk
[bypass] sUltTAjLcfw
[bypass] vr8uu3ZNwzw
[bypass] 0alA

...

[bypass] 58lvMsrOpY0
[bypass] wqX9ix5l7Ec
[bypass] QzpIxAXbGFI
[bypass] TVKSvyga67U
[bypass] bGeEI4LMWSw
[bypass] cXvZVZVwbU4
[bypass] wa7I0f5mjMc
[bypass] yR3o5UpeWus
[bypass] GrVcXa2al1o
[bypass] R0M6_6nueOU
[bypass] zumjSnAUSuc
[bypass] gUJyZiUvrVQ
[bypass] 4N4j3Y4pLhI
[bypass] pcbUnLAA5PQ
[bypass] FegHnR-oX2s
[bypass] nvoSSlvgs0Y
[bypass] aPvUzHhvXVM
[bypass] p4LgsnRorKI
[bypass] tMEcNoyu65I
[bypass] OKK7iqWkLDM
[bypass] WpeFlAWx4t4
[bypass] 9otuQnb-XE4
[bypass] -GsQvfYwvbA
[bypass] TKCGjt1U8xQ
[bypass] cv6iT25ont0
[bypass] lBpWTey55CQ
[bypass] zLn_JT595wM
[bypass] ptF21WLoFEQ
[bypass] ZYrtBWJme-s
[bypass] E9p354SrGP8
[bypass] vDsjksj1Sqk
[bypass] EbWdjmhKOzE
[bypass] 36ebKvIpCo4
[bypass] n-bCO92D0NI
[bypass] Sb6DEtzgI4E
[bypass] g7EoUakibLE
[bypass] -9pgsgrqCYo
[bypass] CW-0UYtefKQ
[bypass] wJw_N1PyJeY
[bypass] QJQzGpulbmA
[bypass] V2WPhr6Wl7Y
[bypass] BXxclYDIHMY
[bypass] YKrej2SuauY
[bypass] tTv6psiE1MY
[bypass] 3TD_tefk6TQ
[bypass] Lmd6Ze1l1CM
[bypass] F8h9xmGkZdE
[bypass] TuVz

[bypass] pDOHqp8Ub2k
[bypass] tL-61uCaHuM
[bypass] jRZZO2J5nS8
[bypass] wwj07IwyFhM
[bypass] kf0NQ6YNMFk
[bypass] qbq7CHSsmDE
[bypass] fRZnejZoxZk
[bypass] ylamsanX4S8
[bypass] shvjuYsc2v4
[bypass] lQz21GA3Wpw
[bypass] U5iBoSnayF4
[bypass] bZaZvOiHF8Q
[bypass] GKcNd207fak
[bypass] AOH8oHHojZ0
[bypass] nsIKZU_HFpA
[bypass] WbzYrg2-XZw
[bypass] zfGFrN-ucHU
[bypass] pSKXTZPkn-s
[bypass] C3bwiLaVE5c
[bypass] 5lyENE7IfLc
[bypass] eKtZyTzl_CI
[bypass] aJeh4adiY1s
[bypass] Z6NpEhFunXs
[bypass] 4OB_miMXJyw
[bypass] K3qIY6Q2sr4
[bypass] N8meVVNPQRA
[bypass] GBkO2NmGhd4
[bypass] Dxo1bO-2oSo
[bypass] Hr6sPnwIVxU
[bypass] PG72Xf4sp_E
[bypass] CQfmcKYbh24
[bypass] NyQ-re3aWGA
[bypass] KrpLVY6XrRc
[bypass] _wX5TdMVpGk
[bypass] qMXLpeB3Opg
[bypass] 1WrE9z2zCy8
[bypass] 3JCdbuJX_BE
[bypass] z5YrHzTXlfE
[bypass] fdMdZmGUIqI
[bypass] _3ob6wFLhUA
[bypass] ler6uQn3aPA
[bypass] qLi_yrv7lK4
[bypass] 56Qdx7BLpX4
[bypass] 9XlxANRHXdM
[bypass] 0Z3rc-hy66c
[bypass] Lhfq0NwGZ0k
[bypass] GSgjGgQBTUw
[bypass] PTNu

[bypass] Aard49eM3pE
[bypass] wUJzcdhRzxY
[bypass] 1MssHBNWlYg
[bypass] wXJ-3NQjTqQ
[bypass] -JC1pTpes_s
[bypass] SQ31_BCDq_U
[bypass] Cknttajvv_8
[bypass] Z8r-hNfHXXY
[bypass] jjgBw8ECC-E
[bypass] 7VzuUW-FdIM
[bypass] XokYZPKrLxc
[bypass] vjVkh1g3Xqs
[bypass] CgXqR3nO30Q
[bypass] QpzOax_ARcI
[bypass] h4IBSseAJlk
[bypass] HbgHE8erPQ0
[bypass] XJ_BDcMZuX8
[bypass] O_BCDzJA69E
[bypass] MRxJ5gMCEAs
[bypass] U89xXsDBDsE
[bypass] IRKRWuWHD0E
[bypass] wjf8S-qckl0
[bypass] 2UyL6sOLb3g
[bypass] hCjONjdhj-E
[bypass] JsHwh8fC2_0
[bypass] ZNtyXeVJu6M
[bypass] SNjx68TCFW0
[bypass] 27l906AKHyc
[bypass] cPXWVqckPgA
[bypass] vyFsRCIIY24
[bypass] ksLpX5Y3rC0
[bypass] G3tGECE3GpE
[bypass] sd5WvtY7yrw
[bypass] DgYzQInAMFE
[bypass] l5KpyMR5q3o
[bypass] 26dlgzh1oDc
[bypass] oLZS8DJiMDo
[bypass] kA6tSIL-0Qk
[bypass] gWvUEex2qEU
[bypass] XSBv9laQROk
[bypass] EEO0h5LmGJI
[bypass] EfCQTUtYWIw
[bypass] 4UKmncGjjBo
[bypass] q8gkh9AFa7U
[bypass] fIbr_EIMswc
[bypass] A1lRG4LEC1s
[bypass] hr2Bt_0lei4
[bypass] APDc

[bypass] VB94ikR3WrE
[bypass] xjv2I0Fi7gs
[bypass] VJnp0SXhS2w
[bypass] 6Lr3_1TZhqM
[bypass] Roe61FV-igc
[bypass] nO4_oJ1EzK4
[bypass] QcYrN1pK9qI
[bypass] UqP_UAgxBKQ
[bypass] 63mG8EP1DHM
[bypass] oUTV7alPazQ
[bypass] LowQJ6JSnt0
[bypass] f5pyUFvVTW8
[bypass] whTS6s_cq5E
[bypass] OIswRAdEqRg
[bypass] uD7uRu58u7k
[bypass] oBjQXsZqZDg
[bypass] c2MYl8dqDNE
[bypass] 2OR1g9-9L3I
[bypass] yKMh08JpOuY
[bypass] 80fTGSCphZg
[bypass] QTe3cSfR1HI
[bypass] SLTsUpYNXUU
[bypass] qiiTTGVI0as
[bypass] RbxBM7f3DcE
[bypass] AKJAQoIJdoQ
[bypass] 2ML__kgXl3s
[bypass] 1Me1Vnb6ziw
[bypass] MdvWfAk8v28
[bypass] F0o-DN9BVe0
[bypass] Z_9UDHr0TJM
[bypass] i5Y0-Cvc3mk
[bypass] eY4v_XdRk-Q
[bypass] ymKtD4img2U
[bypass] mqtHu6EjY1A
[bypass] N4wxQBcqb-U
[bypass] GEkE07HD1Do
[bypass] pO9OnchuPEU
[bypass] xOJWFrH8Wpc
[bypass] PHBtQSNt1IU
[bypass] OA5EmmLMEII
[bypass] lb3Ji1Q6fyk
[bypass] L-Phw3rusmI
[bypass] 3eylt44UY8U
[bypass] QJMzXXLGP9k
[bypass] 26lwwbxEP08
[bypass] uWo-jgfQNGM
[bypass] InW7W0mc_Jg
[bypass] u-z3

iz3cxYzd7Ko HTTP Error 404: Not Found
hoLJxXMmGGw HTTP Error 404: Not Found
uAt79vnKQUc uAt79vnKQUc is unavailable
fG9n52OhTlE fG9n52OhTlE is a private video
KSAShCgX6aI HTTP Error 404: Not Found
jUXylJ8JSWs jUXylJ8JSWs is a private video
sQWfj9CuK54 sQWfj9CuK54 is unavailable
iavx4s2_Ojo HTTP Error 404: Not Found
1_A5R_iFwBM HTTP Error 404: Not Found
l2xVCifgnws HTTP Error 404: Not Found
v2AFNe8W-og v2AFNe8W-og is unavailable
L-9JgMoDdtk HTTP Error 404: Not Found
9ACtZxGev5I HTTP Error 404: Not Found
yV1a9belgD4 HTTP Error 404: Not Found
PG2Swf-Ju8k HTTP Error 404: Not Found
1EaPWzbiVYs 1EaPWzbiVYs is a private video
6nMMgBG9wT0 HTTP Error 404: Not Found
yEdJhTRS9J0 HTTP Error 404: Not Found
6T6w6jm9Zt0 HTTP Error 404: Not Found
1x0vlqAUduY HTTP Error 404: Not Found
TlFrdN64SuQ TlFrdN64SuQ is a private video
https://www.youtube.com/watch?v=TpNQQQE5ti0
download TpNQQQE5ti0 to tempvideo
HjvGhwpuhnA HTTP Error 404: Not Found
I7duYaoyo78 HTTP Error 404: Not Found
Vea8Iu5TMfs HTTP Error 40

In [ ]:
    with open("123.txt",'a+') as fw:
        with open("123.txt",'r+') as fr:
            lines=fr.readlines()
            print(lines.count("123\n"))
            if lines.count("123\n")<5:
                print(1)
                
        fw.write("123"+"\n")
 !wc -l chinese_title_new.csv && wc -l jobs.pkl && cat -v jobs.pkl |grep `cat job_last.txt` -n |cut -f1 -d: && date


In [ ]:
yt=YouTube("https://www.youtube.com/watch?v=S15ZN4c2qLo")
video=sorted(filter(lambda s: s.type == 'video', yt.fmt_streams), key=lambda row: int(row.resolution.replace('p', '')), reverse=True)
print(video)

In [2]:
import pytube
print(pytube.__version__)

10.8.4
